In [1]:
# Import required libraries
import pickle
import copy
import pathlib
import dash
import math
import datetime as dt
import pandas as pd
from dash.dependencies import Input, Output, State, ClientsideFunction
import dash_core_components as dcc
import dash_html_components as html

In [13]:
from jupyter_dash import JupyterDash
JupyterDash.infer_jupyter_proxy_config()

In [3]:
import plotly.express as px
import plotly.graph_objects as go

In [4]:
# Load data
# get relative data folder
PATH = pathlib.Path('./data').parent
DATA_PATH = PATH.joinpath("data").resolve()
PIDAR = pd.read_csv(DATA_PATH.joinpath("pidar.csv"))
AT = pd.read_csv(DATA_PATH.joinpath("DS_Asistencia_Tecnica.csv"))
dfs = [PIDAR,AT]

In [5]:
PIDAR.head()

Unnamed: 0  Unnamed: 0.1  BP  No. VP  \
0           5             5   6       6   
1          16            16  17      17   
2          19            19  20      20   
3          22            22  23      23   
4          24            24  25      25   

                                     Nombre Proyecto        Departamento  \
0  Mejorar las capacidades técnicas de adecuación...               CHOCO   
1  Fortalecer la capacidad productiva y manejo de...                META   
2  Fortalecer la productividad y competitividad d...  NORTE DE SANTANDER   
3  Fortalecer la cadena productiva de café y plát...           ANTIOQUIA   
4  Fortalecimiento de la productividad del cultiv...                META   

           Municipio  Total beneficiarios  Hombres  Mujeres  ...  \
0  CARMEN DEL DARIÉN                   35       30        5  ...   
1            MESETAS                   40       31        9  ...   
2               TIBÚ                   46       31       15  ...   
3            DABEIBA                   25       20        5  ...   
4        LA MACARENA                   28       16       12  ...   

   Valor total cofinanciación ADR  Valor Contrapartida Valor total proyecto  \
0                       250000000            513500000            763500000   
1                       500000000            106600000            606600000   
2                       252785478            351466000            604251478   
3                       401373250            355140000            756513250   
4                       255000000             41570000            296570000   

   Hectáreas  Resolución        Fecha resolución  Vigencia  \
0        100        1219  06/29/2017 12:00:00 AM      2017   
1         40        1250  07/12/2017 12:00:00 AM      2017   
2         92        1453  10/12/2017 12:00:00 AM      2017   
3         69        1351  08/28/2017 12:00:00 AM      2017   
4         93        1401  09/19/2017 12:00:00 AM      2017   

   Lineamiento de consejo directivo AP_ID_ADR  AP_CADENA_PRODUCTIVA_ADR  
0                               NaN         1                  AGRICOLA  
1                               NaN         1                  AGRICOLA  
2                               NaN         1                  AGRICOLA  
3                               NaN         1                  AGRICOLA  
4                               NaN         1                  AGRICOLA  

[5 rows x 23 columns]

In [6]:
AT['CADENA_PRODUCTIVA_ADR'].unique()

array(['MAIZ', 'PLATANO', 'GANADERIA', 'YUCA', 'ARROZ', 'CACAO',
       'ACUICULTURA', 'NISPERO', 'AGRICOLA', 'COMERCIALIZACION',
       'CITRICOS', 'AGROPECUARIO', 'MANGO', 'PAPAYA', 'APICULTURA',
       'AVICULTURA', 'HORTOFRUTICOLA', 'LACTEO', 'CAFE', 'ACHIRA',
       'FRESA', 'GRANADILLA', 'TOMATE', 'ARVEJA', 'PAPA', 'AGUACATE',
       'COCO', 'PECUARIO', 'FRIJOL', 'CEBOLLA', 'MORA',
       'PLANTAS AROMATICAS, MEDICINALES, ESPECIAS Y SEMILLAS', 'CEBADA',
       'TRIGO', 'TOMATE DE ARBOL', 'UCHUVA', 'GULUPA', 'FIQUE', 'LULO'],
      dtype=object)

In [7]:
#Cargar Geo Json
import json
with open('Colombia.geo.json') as f:
    counties = json.load(f)
#Cambiar los nombre de los proyectos del df acorde con el geojson
Departamentos = []
geocol = counties.copy()
for man in geocol['features']:
    Departamentos.append(man['properties']['NOMBRE_DPT'])
    man['id']=man['properties']['NOMBRE_DPT']

for ii in range(len(dfs)):
    #Nariño genera problemas por eos lo colocamos con este nombre
    dfs[ii].loc[dfs[ii]['Departamento'].str.find('NARIÑO')>=0,'Departamento']='NARIÃ‘O'

In [8]:
# #Agrupar por departamtento cada una de las columnas
dff = PIDAR.groupby('Departamento').sum().reset_index()
dff.head()

Departamento  Unnamed: 0  Unnamed: 0.1    BP  No. VP  Total beneficiarios  \
0    ANTIOQUIA         930           930  1316    1116                  408   
1       ARAUCA         178           178   346     220                   25   
2    ATLANTICO          47            47    49      49                  140   
3      BOLIVAR         362           362   429     429                  538   
4      BOLÍVAR         126           126   150     150                   94   

   Hombres  Mujeres  Total Víctimas  Valor cofinanciado ADR  \
0      267      141             132              4162445250   
1       16        9              14               375523000   
2      103       37              15              1505613100   
3      517       21             350              6122804000   
4       84       10              38               977966000   

   Valor total cofinanciación ADR  Valor Contrapartida  Valor total proyecto  \
0                      4162445250           1916939196            6079384446   
1                       375523000            185194000             560717000   
2                      1505613100            350547400            1856160500   
3                      6122804000           1317642000            7440446000   
4                       977966000            282000000            1259966000   

   Hectáreas  Resolución  Vigencia  AP_ID_ADR  
0        351        5929     16135          8  
1         25         624      2018          1  
2        140         104      2017          1  
3       1139        1187      6051          3  
4         94           8      2018          1

In [9]:
fig = px.choropleth_mapbox(dff,                                      #Data
                                   locations='Departamento',                              #Column containing the identifiers used in the GeoJSON file 
                                   color='Valor total cofinanciación ADR',                        #Column giving the color intensity of the region
                                   geojson=geocol,                                        #The GeoJSON file
                                   zoom=3,                                                #Zoom
                                   mapbox_style="carto-positron",                         #Mapbox style, for different maps you need a Mapbox account and a token
                                   range_color=(0, dff['Valor cofinanciado ADR'].max()), 
                                   center={"lat":4.7110, "lon": -74.0721},                #Center
                                   color_continuous_scale="Viridis",                      #Color Scheme
                                   opacity=0.5,                                           #Opacity of the map
                                  )
fig.update_layout(transition_duration=500, margin={'l': 40, 'b': 30, 't': 10, 'r': 0},
                          height=450)

In [10]:
#Cargar la informacion e indicadores necesariso para el dash

##Cargar el logo del dashboard
import base64
test_png = './assets/my-image.png'
test_base64 = base64.b64encode(open(test_png, 'rb').read()).decode('ascii')

##Cargar los indicadores que van en la lista desplegable
available_indicators = ['Total beneficiarios', 'Hombres', 'Mujeres',
       'Total Víctimas', 'Valor cofinanciado ADR', 'Valor encargo fiduciario',
       'Valor total cofinanciación ADR', 'Valor Contrapartida',
       'Valor total proyecto', 'Hectáreas']

##Cargar la lista de años que tenemos disponible para el slider
YEARS = PIDAR['Vigencia'].unique()

In [11]:
from controls import COUNTIES, WELL_STATUSES, WELL_TYPES, WELL_COLORS
well_type_options = [
    {"label": str(WELL_TYPES[well_type]), "value": str(well_type)}
    for well_type in WELL_TYPES
]
print(well_type_options)

[{'label': 'ANTIOQUIA', 'value': 'AN'}, {'label': 'ARAUCA', 'value': 'AR'}, {'label': 'ATLANTICO', 'value': 'AT'}, {'label': 'BOLIVAR', 'value': 'BV'}, {'label': 'BOLÍVAR', 'value': 'BB'}, {'label': 'BOYACA', 'value': 'BY'}, {'label': 'CALDAS', 'value': 'CL'}, {'label': 'CAUCA', 'value': 'CU'}, {'label': 'CESAR', 'value': 'CS'}, {'label': 'CHOCO', 'value': 'CO'}, {'label': 'CORDOBA', 'value': 'CR'}, {'label': 'CUNDINAMARCA', 'value': 'CN'}, {'label': 'GUAINIA', 'value': 'GA'}, {'label': 'HUILA', 'value': 'HL'}, {'label': 'LA_GUAJIRA', 'value': 'LG'}, {'label': 'MAGDALENA', 'value': 'MD'}, {'label': 'META', 'value': 'MT'}, {'label': 'NARIÃ‘O', 'value': 'NO'}, {'label': 'NORTE DE SANTANDER', 'value': 'NS'}, {'label': 'QUINDIO', 'value': 'QD'}, {'label': 'SANTANDER', 'value': 'ST'}, {'label': 'TOLIMA', 'value': 'TL'}, {'label': 'VALLE DEL CAUCA', 'value': 'VC'}, {'label': 'VAUPES', 'value': 'VP'}, {'label': 'VICHADA', 'value': 'VH'}]


In [ ]:
app = dash.Dash(
    __name__, meta_tags=[{"name": "viewport", "content": "width=device-width"}]
)
server = app.server


# Multi-dropdown options
from controls import COUNTIES, WELL_STATUSES, WELL_TYPES, WELL_COLORS

# Create controls
county_options = [
    {"label": str(COUNTIES[county]), "value": str(county)} for county in COUNTIES
]

well_status_options = [
    {"label": str(WELL_STATUSES[well_status]), "value": str(well_status)}
    for well_status in WELL_STATUSES
]

well_type_options = [
    {"label": str(WELL_TYPES[well_type]), "value": str(well_type)}
    for well_type in WELL_TYPES
]

# Create global chart template
layout = dict(
    autosize=True,
    automargin=True,
    margin=dict(l=30, r=30, b=20, t=40),
    hovermode="closest",
    plot_bgcolor="#F9F9F9",
    paper_bgcolor="#F9F9F9",
    legend=dict(font=dict(size=10), orientation="h"),
    title="Satellite Overview",
    mapbox=dict(
        style="light",
        center=dict(lon=-78.05, lat=42.54),
        zoom=7,
    ),
)

# Create app layout
app.layout = html.Div(
    [
        dcc.Store(id="aggregate_data"),
        # empty Div to trigger javascript file for graph resizing
        html.Div(id="output-clientside"),
        html.Div(
            [
                html.Div(
                    [
                        html.Img(
                            src='data:image/png;base64,{}'.format(test_base64),
                            id="plotly-image",
                            style={
                                "height": "60px",
                                "width": "auto",
                                "margin-bottom": "25px",
                            },
                        )
                    ],
                    className="one-third column",
                ),
                html.Div(
                    [
                        html.Div(
                            [
                                html.H3(
                                    "PIDAR projects",
                                    style={"margin-bottom": "0px"},
                                ),
                                html.H5(
                                    "Comprehensive Agricultural Development Plans with a Territorial Approach \
                (PIDAR for its Spanish acronym)", style={"margin-top": "0px"}
                                ),
                            ]
                        )
                    ],
                    className="one-half column",
                    id="title",
                ),
                html.Div(
                    [
                        html.A(
                            html.Button("Learn More", id="learn-more-button"),
                            href="https://www.adr.gov.co/Paginas/Agencia-de-Desarrollo-Rural.aspx",
                        )
                    ],
                    className="one-third column",
                    id="button",
                ),
            ],
            id="header",
            className="row flex-display",
            style={"margin-bottom": "25px"},
        ),
        html.Div(
            [
                html.Div(
                    [
                        html.P(
                            "Filter by construction date (or select range in histogram):",
                            className="control_label",
                        ),
                        dcc.RangeSlider(
                            id="year_slider",
                            min=min(YEARS),
                            max=max(YEARS),
                            value=[min(YEARS), max(YEARS)],
                            className="dcc_control",
                            marks={
                                        str(year): {
                                            "label": str(year),
                                            "style": {"color": "#7fafdf"},
                                        }
                                        for year in YEARS
                                    }
                        ),
                        html.P("Filter by type project:", className="control_label"),
                        dcc.RadioItems(
                            id="well_status_selector",
                            options=[
                                {"label": "All ", "value": "all"},
                                {"label": "Active only ", "value": "active"},
                                {"label": "Customize ", "value": "custom"},
                            ],
                            value="active",
                            labelStyle={"display": "inline-block"},
                            className="dcc_control",
                        ),
                        dcc.Dropdown(
                            id="well_statuses",
                            options=well_status_options,
                            multi=True,
                            value=list(WELL_STATUSES.keys()),
                            className="dcc_control",
                        ),
                        dcc.Checklist(
                            id="lock_selector",
                            options=[{"label": "Lock camera", "value": "locked"}],
                            className="dcc_control",
                            value=[],
                        ),
                        html.P("Filter by department:", className="control_label"),
                        dcc.RadioItems(
                            id="well_type_selector",
                            options=[
                                {"label": "All ", "value": "all"},
                                {"label": "Productive only ", "value": "productive"},
                                {"label": "Customize ", "value": "custom"},
                            ],
                            value="productive",
                            labelStyle={"display": "inline-block"},
                            className="dcc_control",
                        ),
                        dcc.Dropdown(
                            id="well_types",
                            options=well_type_options,
                            multi=True,
                            value=list(WELL_TYPES.keys()),
                            className="dcc_control",
                        ),
                    ],
                    className="pretty_container four columns",
                    id="cross-filter-options",
                ),
                html.Div(
                    [
                        html.Div(
                            [
                                html.Div(
                                    [html.H6(id="well_text"), html.P("No. of projects")],
                                    id="wells",
                                    className="mini_container",
                                ),
                                html.Div(
                                    [html.H6(id="gasText"), html.P("Hectareas")],
                                    id="gas",
                                    className="mini_container",
                                ),
                                html.Div(
                                    [html.H6(id="oilText"), html.P("Beneficiarios")],
                                    id="oil",
                                    className="mini_container",
                                ),
                                html.Div(
                                    [html.H6(id="waterText"), html.P("Total cofinanciado")],
                                    id="water",
                                    className="mini_container",
                                ),
                            ],
                            id="info-container",
                            className="row container-display",
                        ),
                        html.Div(
                            [dcc.Graph(id="count_graph")],
                            id="countGraphContainer",
                            className="pretty_container",
                        ),
                    ],
                    id="right-column",
                    className="eight columns",
                ),
            ],
            className="row flex-display",
        ),
        html.Div(
            [
                html.Div(
                    [dcc.Graph(id="main_graph")],
                    className="pretty_container seven columns",
                ),
                html.Div(
                    [dcc.Graph(id="individual_graph")],
                    className="pretty_container five columns",
                ),
            ],
            className="row flex-display",
        ),
        html.Div(
            [
                html.Div(
                    [dcc.Graph(id="pie_graph")],
                    className="pretty_container seven columns",
                ),
                html.Div(
                    [dcc.Graph(id="aggregate_graph")],
                    className="pretty_container five columns",
                ),
            ],
            className="row flex-display",
        ),
    ],
    id="mainContainer",
    style={"display": "flex", "flex-direction": "column"},
)


# Helper functions
def human_format(num):
    if num == 0:
        return "0"

    magnitude = int(math.log(num, 1000))
    mantissa = str(int(num / (1000 ** magnitude)))
    return mantissa + ["", "K", "M", "G", "T", "P"][magnitude]


def filter_dataframe(df, well_statuses, well_types, year_slider):
    dff = df[
        df['Lineamiento de consejo directivo'].isin(well_statuses)
        & df['Departamento'].isin(well_types)
        & (df["Vigencia"] > year_slider[0])
        & (df["Vigencia"] < year_slider[1])
    ]
    return dff


def produce_individual(api_well_num):
    try:
        points[api_well_num]
    except:
        return None, None, None, None

    index = list(
        range(min(points[api_well_num].keys()), max(points[api_well_num].keys()) + 1)
    )
    gas = []
    oil = []
    water = []

    for year in index:
        try:
            gas.append(points[api_well_num][year]["Gas Produced, MCF"])
        except:
            gas.append(0)
        try:
            oil.append(points[api_well_num][year]["Oil Produced, bbl"])
        except:
            oil.append(0)
        try:
            water.append(points[api_well_num][year]["Water Produced, bbl"])
        except:
            water.append(0)

    return index, gas, oil, water

def produce_aggregate(dff):
    
    index = len(dff)
    gas = sum(dff['Total beneficiarios'])
    oil = sum(dff['Hectáreas'])
    water = sum(dff['Valor total cofinanciación ADR'])

    return index, gas, oil, water


# # Create callbacks
# app.clientside_callback(
#     ClientsideFunction(namespace="clientside", function_name="resize"),
#     Output("output-clientside", "children"),
#     [Input("count_graph", "figure")],
# )

@app.callback(
    Output("aggregate_data", "data"),
    [
        Input("well_statuses", "value"),
        Input("well_types", "value"),
        Input("year_slider", "value"),
    ],
)
def update_production_text(well_statuses, well_types, year_slider):

    dff = filter_dataframe(PIDAR, well_statuses, well_types, year_slider)
    index, gas, oil, water = produce_aggregate(dff)
    return [gas, oil, human_format(water)]

# Selectors -> well text
@app.callback(
    Output("well_text", "children"),
    [
        Input("well_statuses", "value"),
        Input("well_types", "value"),
        Input("year_slider", "value"),
    ],
)
def update_well_text(well_statuses, well_types, year_slider):
    df3 = filter_dataframe(PIDAR, well_statuses, well_types, year_slider)
    return df3.shape[0]

@app.callback(
    [
        Output("gasText", "children"),
        Output("oilText", "children"),
        Output("waterText", "children"),
    ],
    [Input("aggregate_data", "data")],
)
def update_text(data):
    return data[0], data[1], data[2]

@app.callback(
    Output("main_graph", "figure"),
    [Input("well_statuses", "value"),
     Input("well_types", "value"),
     Input("year_slider", "value")
    ]
)
        
def update_graph(well_statuses, well_types, year_slider):
        dff = filter_dataframe(PIDAR, well_statuses, well_types, year_slider)
        
        fig = px.choropleth_mapbox(PIDAR,                                      #Data
                                   locations='Departamento',                              #Column containing the identifiers used in the GeoJSON file 
                                   color='Valor cofinanciado ADR',                        #Column giving the color intensity of the region
                                   geojson=geocol,                                        #The GeoJSON file
                                   zoom=3,                                                #Zoom
                                   mapbox_style="carto-positron",                         #Mapbox style, for different maps you need a Mapbox account and a token
                                   range_color=(0, dff['Valor cofinanciado ADR'].max()), 
                                   center={"lat":4.7110, "lon": -74.0721},                #Center
                                   color_continuous_scale="Viridis",                      #Color Scheme
                                   opacity=0.5,                                           #Opacity of the map
                                  )
        fig.update_layout(transition_duration=500, margin={'l': 40, 'b': 30, 't': 10, 'r': 0},
                          height=450)
        return fig

    
app.run_server(debug=True, use_reloader=False)

Running on http://127.0.0.1:8050/
Running on http://127.0.0.1:8050/
Running on http://127.0.0.1:8050/
Running on http://127.0.0.1:8050/
Debugger PIN: 865-219-582
Debugger PIN: 865-219-582
Debugger PIN: 865-219-582
Debugger PIN: 865-219-582
 * Serving Flask app "__main__" (lazy loading)
 * Environment: production
   Use a production WSGI server instead.
 * Debug mode: on
